# GAN Preprocesamiento de datos

In [1]:
from dataset.modules.music_dataset import TorchMusicDataset
import librosa
import io
import os
import tensorflow as tf
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from IPython.display import Audio

import torch
import torch.nn as nn
import torch.optim as optim

import librosa
import librosa.display
import IPython.display as ipd
import soundfile as sf

import torch
import torch.nn as nn
import torch.optim as optim
import librosa
import librosa.display
import numpy as np
import matplotlib.pyplot as plt
import pickle

from torchsummary import summary

In [2]:
dataset = TorchMusicDataset("cleaned_data")
obj = dataset.__getitem__(0)

dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])


In [3]:
def audio_to_stft(audio_time_series, sr=44100, n_fft=1024, hop_length=512):
    """
    Convierte un audio time series a un STFT.

    Parámetros:
    audio_time_series (numpy array): Audio time series.
    sr (int): Frecuencia de muestreo (default=44100).
    n_fft (int): Tamaño de la ventana de Fourier (default=2048).
    hop_length (int): Longitud del salto entre ventanas (default=512).

    Retorna:
    stft (numpy array): STFT del audio.
    """
    stft = librosa.stft(audio_time_series, n_fft=n_fft, hop_length=hop_length)
    return stft

In [4]:
from dataset.modules.music_dataset import TorchMusicDataset

dataset = TorchMusicDataset("cleaned_data")
songs = []
for i in range(700):
    obj = dataset.__getitem__(i)
    song = audio_to_stft(obj['time_series'].numpy(), sr=44100, n_fft=1024, hop_length=512)
    # song = obj['time_series'].numpy()[:-7]
    songs.append(song)

dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])
dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])
dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])
dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])
dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])
dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])
dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])
dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])
dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])
dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])
dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])
dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])
dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])
dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])
dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])
dict_keys(['song_id', 'genre_id', 'genre', 'time_series'])
dict_keys(['song_id', 'genre_id', 'genre', 'time_series'

In [5]:
import numpy as np
import librosa
import librosa.display
import IPython.display as ipd
import soundfile as sf

# Parámetros de STFT 
n_fft = 1024
hop_length = 512
sr = 44100  

# Separar magnitud y fase
magnitude_list = [np.abs(stft) for stft in songs]

all_magnitudes = np.concatenate([mag.flatten() for mag in magnitude_list])

global_magnitude_mean = np.mean(all_magnitudes)
global_magnitude_std = np.std(all_magnitudes)

del all_magnitudes


phase_list = [np.angle(stft) for stft in songs]

all_phases = np.concatenate([ph.flatten() for ph in phase_list])

global_phase_mean = np.mean(all_phases)
global_phase_std = np.std(all_phases)

del all_phases

print(f"Global Magnitude Mean: {global_magnitude_mean}, Global Magnitude Std: {global_magnitude_std}")
print(f"Global Phase Mean: {global_phase_mean}, Global Phase Std: {global_phase_std}")

def normalize_stft(magnitude, phase, magnitude_mean, magnitude_std, phase_mean, phase_std):
    normalized_magnitude = (magnitude - magnitude_mean) / magnitude_std
    normalized_phase = (phase - phase_mean) / phase_std
    return normalized_magnitude, normalized_phase

normalized_stfts = [normalize_stft(mag, ph, global_magnitude_mean, global_magnitude_std, global_phase_mean, global_phase_std) for mag, ph in zip(magnitude_list, phase_list)]

del magnitude_list, phase_list

# Convertir a tensores de PyTorch
magnitude_tensors = [torch.tensor(mag, dtype=torch.float32).unsqueeze(0).unsqueeze(0) for mag, _ in normalized_stfts]
phase_tensors = [torch.tensor(ph, dtype=torch.float32).unsqueeze(0).unsqueeze(0) for _, ph in normalized_stfts]

# Guardar la media y la desviación estandar
with open('gan/global_stft_stats.pkl', 'wb') as f:
    pickle.dump({'magnitude_mean': global_magnitude_mean, 'magnitude_std': global_magnitude_std, 'phase_mean': global_phase_mean, 'phase_std': global_phase_std}, f)

def denormalize_stft(magnitude, phase, magnitude_mean, magnitude_std, phase_mean, phase_std):
    denormalized_magnitude = magnitude * magnitude_std + magnitude_mean
    denormalized_phase = phase * phase_std + phase_mean
    return denormalized_magnitude, denormalized_phase

# Ejemplo de reconstruccion
generated_magnitude = magnitude_tensors[0].numpy().squeeze()
generated_phase = phase_tensors[0].numpy().squeeze()

denormalized_magnitude, denormalized_phase = denormalize_stft(generated_magnitude, generated_phase, global_magnitude_mean, global_magnitude_std, global_phase_mean, global_phase_std)

denormalized_stft = denormalized_magnitude * np.exp(1j * denormalized_phase)

reconstructed_audio = librosa.istft(denormalized_stft, hop_length=hop_length, win_length=n_fft)

sf.write('reconstructed_audio.wav', reconstructed_audio, samplerate=sr)
ipd.Audio('reconstructed_audio.wav')

Global Magnitude Mean: 0.7868581414222717, Global Magnitude Std: 4.0197672843933105
Global Phase Mean: 0.008972293697297573, Global Phase Std: 1.8158828020095825


In [6]:
generated_magnitude = magnitude_tensors[1].numpy().squeeze()
generated_phase = phase_tensors[1].numpy().squeeze()

denormalized_magnitude, denormalized_phase = denormalize_stft(generated_magnitude, generated_phase, global_magnitude_mean, global_magnitude_std, global_phase_mean, global_phase_std)

denormalized_stft = denormalized_magnitude * np.exp(1j * denormalized_phase)

reconstructed_audio = librosa.istft(denormalized_stft, hop_length=hop_length, win_length=n_fft)

sf.write('reconstructed_audio.wav', reconstructed_audio, samplerate=sr)
ipd.Audio('reconstructed_audio.wav')

In [7]:
# Activar CUDA
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [8]:
# Parámetros de entrenamiento
latent_dim = 100
batch_size = 8
num_epochs = 100
lr = 0.0002

# Crear DataLoader y Dataset
stft_tensors = [torch.cat([mag, ph], dim=1) for mag, ph in zip(magnitude_tensors, phase_tensors)]
stft_dataset = torch.utils.data.TensorDataset(torch.cat(stft_tensors))
stft_loader = torch.utils.data.DataLoader(stft_dataset, batch_size=batch_size, shuffle=True)

In [9]:
# Guardamos porque haremos el entrenamiento en Colab
torch.save(stft_dataset, 'gan/stft_dataset.pt')

In [10]:
len(stft_dataset)

700

In [11]:
for data in stft_loader:
    print(f"Shape of the data: {data[0].shape}")
    break  
    
print(f"Length of the dataset: {len(dataset)}")

Shape of the data: torch.Size([8, 2, 513, 2582])
Length of the dataset: 700
